In [32]:
import openai
import tiktoken
import tempfile
import IPython
import structlog
from gtts import gTTS
import requests
logger = structlog.getLogger()
openai.api_key_path = '/home/jong/.openai_key'

In [63]:
class ElevenLabsTTS:
    WOMAN = 'EXAVITQu4vr4xnSDxMaL'
    MAN = 'VR6AewLTigWG4xSOukaG'
    def __init__(self, api_key_fpath='/home/jong/.elevenlabs_apikey', voice_id=None):
        with open(api_key_fpath) as f:
            self.api_key = f.read().strip()
        self._voice_id = voice_id or self.WOMAN
        self.uri = "https://api.elevenlabs.io/v1/text-to-speech/" + self._voice_id
    def tts(self, text):
        headers = {
            "accept": "audio/mpeg",
            "xi-api-key": self.api_key,
        }
        payload = {
            "text": text,
        }
        return requests.post(self.uri, headers=headers, json=payload).content

In [64]:
class Chat:
    def __init__(self, topic, podcast="award winning NPR", max_length=4096//4, hosts=['Tom', 'Jen']):
        system = f"You are an {podcast} podcast with hosts {hosts[0]} and {hosts[1]}."
        self._system = system
        self._topic = topic
        self._max_length = max_length
        self._hosts = hosts
        self._history = [
            {"role": "system", "content": self._system},
            {"role": "user", "content": f"Generate a podcast episode about {topic}, including history and other fun facts. Reference published scientific journals."},
        ]
        self._tts_h1 = ElevenLabsTTS(voice_id=ElevenLabsTTS.MAN)
        self._tts_h2 = ElevenLabsTTS(voice_id=ElevenLabsTTS.WOMAN)

    @classmethod
    def num_tokens_from_messages(cls, messages, model="gpt-3.5-turbo"):
        """Returns the number of tokens used by a list of messages."""
        encoding = tiktoken.encoding_for_model(model)
        num_tokens = 0
        for message in messages:
            num_tokens += 4  # every message follows <im_start>{role/name}\n{content}<im_end>\n
            for key, value in message.items():
                num_tokens += len(encoding.encode(value))
                if key == "name":  # if there's a name, the role is omitted
                    num_tokens += -1  # role is always required and always 1 token
        num_tokens += 2  # every reply is primed with <im_start>assistant
        return num_tokens
        
    def message(self, next_msg=None):
        # TODO: Optimize this if slow through easy caching
        while len(self._history) > 1 and self.num_tokens_from_messages(self._history) > self._max_length:
            logger.info(f'Popping message: {self._history.pop(1)}')
        if next_msg is not None:
            self._history.append({"role": "user", "content": next_msg})
        logger.info('requesting openai...')
        resp = openai.ChatCompletion.create(
            model="gpt-3.5-turbo",
            messages=self._history,
        )
        logger.info('received openai...')
        text = resp.choices[0].message.content
        self._history.append({"role": "assistant", "content": text})
        return text

    def text2speech(self, text, spacing_ms=350):
        # with tempfile.TemporaryDirectory(delete=False) as tmpdir:
        tmpdir = '/tmp'
        if True:
            i = 0
            def write_audio(msg, i, voice, **kwargs):
                logger.info(f'requesting tts {i=} {tmpdir=}')
                # s = gTTS(msg, **kwargs)
                s = voice.tts(msg)
                # with open(f'{tmpdir}/{i}.mpeg', 'wb') as f:
                #     f.write(s)
                logger.info(f'received tts {i=}')
                return s
                

            text = text.replace('\n', '!!!LINEBREAK!!!').replace('\\', '')
            # Build text one at a time
            currline, currname = "", self._hosts[0]
            name2tld = {self._hosts[0]: 'co.uk', self._hosts[1]: 'com'}
            name2voice = {self._hosts[0]: self._tts_h1, self._hosts[1]: self._tts_h2}
            audios = []
            for line in text.split("!!!LINEBREAK!!!"):
                if not line.strip(): continue
                if line.startswith(f"{self._hosts[0]}: ") or line.startswith(f"{self._hosts[1]}: "):
                    if currline:
                        audios.append(write_audio(currline, i, name2voice[currname], lang='en', tld=name2tld[currname]))
                        i += 1
                    currline = line[4:]
                    currname = line[:3]
                else:
                    currline += line
            if currline:
                audios.append(write_audio(currline, i, name2voice[currname], lang='en', tld=name2tld[currname]))
                i+=1
            # Concat files
            logger.info('concatting audio')
            audio = b''.join(audios)
#             from pydub import AudioSegment
#             total_sound = None
#             for mp3_i in range(i):
#                 sound = AudioSegment.from_file(f"{tmpdir}/{mp3_i}.mpeg", "mpeg")
#                 if total_sound is None:
#                     total_sound = sound
#                 else:
#                     total_sound = total_sound + AudioSegment.silent(duration=spacing_ms) + sound

#             total_sound.export(f"{tmpdir}/total.mpeg", format="mpeg")
            logger.info('done with audio!')
            display(IPython.display.Audio(audio, autoplay=True))
            
    def step(self, msg=None):
        msg = self.message(msg)
        self.text2speech(msg)
        return msg

In [ ]:
chat = Chat('Ancestory and Evolution of Sheep', podcast='CNN podcast')
chat.step()

2023-03-04 12:50:44 [info     ] requesting openai...
2023-03-04 12:50:56 [info     ] received openai...
2023-03-04 12:50:56 [info     ] requesting tts i=0 tmpdir='/tmp'
2023-03-04 12:50:59 [info     ] received tts i=0
2023-03-04 12:50:59 [info     ] requesting tts i=1 tmpdir='/tmp'


In [16]:
chat.step('Episode on Vermont, including an interview with a former governor.')

'"Welcome to our NPR podcast, where Tom and I explore the diverse culture and history of the US. In today\'s episode, we\'ll be delving deep into the picturesque state of Vermont. Known for maple syrup, fall foliage, and quaint villages, Vermont has a rich history and interesting political background." \n\nTom chimes in, "And we\'re lucky enough to have a special guest with us today, former Governor Peter Shumlin, who\'ll give us some insight into what it was like to lead this unique state. Governor Shumlin, welcome to the show!"\n\n"Thanks for having me," says Governor Shumlin. \n\n"So, Governor Shumlin, can you tell us a bit about what makes Vermont so special?" Jen asks. \n\n"Well, I think what makes Vermont so special is its sense of community. Over the years, Vermonters have come together to support one another in times of need, from disaster relief to economic challenges. This support is what makes Vermont such a great place to live and work," Governor Shumlin replies. \n\nJen ad

In [28]:
cnn_chat = Chat('penguin social hierarchy', podcast='CNN')
cnn_chat.step()

2023-03-04 11:42:09 [info     ] requesting openai...
2023-03-04 11:42:24 [info     ] received openai...
2023-03-04 11:42:24 [info     ] requesting tts i=0
2023-03-04 11:42:24 [info     ] received tts i=0
2023-03-04 11:42:25 [info     ] requesting tts i=1
2023-03-04 11:42:25 [info     ] received tts i=1
2023-03-04 11:42:26 [info     ] requesting tts i=2
2023-03-04 11:42:26 [info     ] received tts i=2
2023-03-04 11:42:27 [info     ] requesting tts i=3
2023-03-04 11:42:27 [info     ] received tts i=3
2023-03-04 11:42:30 [info     ] requesting tts i=4
2023-03-04 11:42:30 [info     ] received tts i=4
2023-03-04 11:42:32 [info     ] requesting tts i=5
2023-03-04 11:42:32 [info     ] received tts i=5
2023-03-04 11:42:33 [info     ] requesting tts i=6
2023-03-04 11:42:33 [info     ] received tts i=6
2023-03-04 11:42:37 [info     ] requesting tts i=7
2023-03-04 11:42:37 [info     ] received tts i=7
2023-03-04 11:42:38 [info     ] requesting tts i=8
2023-03-04 11:42:38 [info     ] received tts 

'Tom: Welcome to the CNN Podcast, I\'m Tom and I\'m joined by Jen. Today we\'ll be discussing penguin social hierarchy, their history and other fun facts.\n\nJen: Yes, penguins are fascinating creatures and we can learn a lot about their behavior and social structure by observing their interactions in the wild.\n\nTom: That\'s right, Jen. Studies have shown that penguins have a highly structured social hierarchy, with each individual penguin occupying a specific place within the group.\n\nJen: This social hierarchy is usually determined by a combination of factors, including age, strength, size, and overall health. The strongest and fittest penguins usually occupy the highest positions in the hierarchy, while the weaker and older penguins often rank lower.\n\nTom: Researchers have also found that penguins will often form groups or cliques within their social structures, with some penguins forming bonds with others in the same rank, while others may try to climb the ranks by forming all

In [29]:
cnn_chat.step("Long detailed episode about the social hierarchy of elephants.")

2023-03-04 11:45:26 [info     ] requesting openai...
2023-03-04 11:45:40 [info     ] received openai...
2023-03-04 11:45:40 [info     ] requesting tts i=0
2023-03-04 11:45:40 [info     ] received tts i=0
2023-03-04 11:45:41 [info     ] requesting tts i=1
2023-03-04 11:45:41 [info     ] received tts i=1
2023-03-04 11:45:43 [info     ] requesting tts i=2
2023-03-04 11:45:43 [info     ] received tts i=2
2023-03-04 11:45:43 [info     ] requesting tts i=3
2023-03-04 11:45:43 [info     ] received tts i=3
2023-03-04 11:45:44 [info     ] requesting tts i=4
2023-03-04 11:45:44 [info     ] received tts i=4
2023-03-04 11:45:46 [info     ] requesting tts i=5
2023-03-04 11:45:46 [info     ] received tts i=5
2023-03-04 11:45:48 [info     ] requesting tts i=6
2023-03-04 11:45:48 [info     ] received tts i=6
2023-03-04 11:45:49 [info     ] requesting tts i=7
2023-03-04 11:45:49 [info     ] received tts i=7
2023-03-04 11:45:51 [info     ] requesting tts i=8
2023-03-04 11:45:51 [info     ] received tts 

"Tom: Welcome to the CNN Podcast, I'm Tom and I'm joined by Jen. Today we'll be discussing the social hierarchy of elephants, their complex and fascinating relationships and behaviors.\n\nJen: That's right, Tom. Elephants are highly intelligent and social animals, with a highly structured and matriarchal social hierarchy.\n\nTom: Elephants live in close-knit family units called herds, which are typically led by a dominant female elephant known as the matriarch.\n\nJen: The matriarch is responsible for leading the group and making important decisions such as where to find food and water as well as where to rest and sleep.\n\nTom: The matriarch is usually the oldest and largest female in the group, and she maintains her leadership position through a combination of strength, intelligence, and knowledge.\n\nJen: Elephants also have a system of relational ranking within their herds. This means that each individual elephant has a specific rank within the group, which is determined by their a

In [31]:
display(IPython.display.Audio(f"ht.mp3", autoplay=True))

In [73]:
chat = Chat("Sloths", hosts=['Noa', 'Guy'])
chat.step()

'[Opening music]\n\nNoa: Welcome to the show, I’m Noa.\n\nGuy: And I’m Guy. Today we’re talking about a creature that moves at a glacial pace but has captured the hearts and imaginations of people all over the world. We’re talking, of course, about…\n\nNoa and Guy (in unison): Sloths!\n\nGuy: Sloths are fascinating creatures, with their seemingly lackadaisical lifestyle and cute, often goofy faces. But there’s so much more to these animals than their outward appearance.\n\nNoa: That’s right, Guy. According to the International Union for Conservation of Nature, there are six different species of sloths, four of which are found in Central and South America.\n\nGuy: Let’s start with some history. Did you know that sloths were first documented by European explorers in the 15th and 16th centuries?\n\nNoa: Yeah, and fun fact: they were initially mistaken for monkeys. It wasn’t until the 18th century that scientists began to recognize them as a distinct group of animals.\n\nGuy: The two-toed 

In [74]:
chat.step('Make another funny episode about Sloths. Do not repeat any information from before.')

'[Opening music]\n\nNoa: Welcome to the show, I’m Noa.\n\nGuy: And I’m Guy. Today, we’re talking about the laziest, sleepiest, and cutest animals on the planet: sloths!\n\nNoa: Speaking of laziness, did you know that sloths sleep for up to 15 hours a day? That’s nearly two-thirds of their entire life!\n\nGuy: Don’t forget about their slow movement. Sloths move so slowly that scientists once clocked one traveling just seven feet in a minute.\n\nNoa: And did you know that sloths have a symbiotic relationship with moths? Sloths grow algae on their fur, which the moths then eat.\n\nGuy: Wait, what? Algae? On their fur? That’s disgusting!\n\nNoa: Hey, don’t be sloth-shaming. Besides, if you think that’s gross, just wait until you hear about the sloth’s digestive system.\n\nGuy: I don’t think I want to hear this.\n\nNoa: Sloths only poop once a week, and it can take them up to a month to digest one meal.\n\nGuy: Ew, that’s seriously gross.\n\nNoa: Hey, you’re the one who wanted to talk about

In [50]:
msg = chat.message('Tell me other things about yogurt and make it funny')
Chat.text2speech(msg)

In [51]:
chat._history

[{'role': 'system',
  'content': 'You are an award winning NPR podcast with hosts Tom and Jen.'},
 {'role': 'user',
  'content': 'Generate a podcast episode about Yogurt, including history and other fun facts. Reference published scientific journals.'},
 {'role': 'assistant',
  'content': 'Tom: Welcome back to our podcast, today we are discussing Yogurt! A dairy product that has been around for thousands of years.\n\nJen: That’s right, Tom. In fact, the origins of yogurt can be traced back to the Neolithic period over 10,000 years ago. Nomadic tribes in Central Asia discovered that milk left to ferment in animal skins preserved the milk and created a tasty and nutritious sour milk product, which we now know as yogurt.\n\nTom: That’s fascinating. I had no idea yogurt had such a rich history. What are some of the health benefits of eating yogurt?\n\nJen: Well, according to research published in the American Journal of Clinical Nutrition, yogurt is a great source of calcium, protein, and 

In [10]:
"""
TODO:
    Make web server and send mp3 to frontend
    Make frontend and play results
"""

'\nTODO:\n'